
File: 05-wtp.py


Michel Bierlaire

Wed Aug 14 08:12:32 2024



In [ ]:

import numpy as np
from IPython.core.display_functions import display
from biogeme.biogeme import BIOGEME
from biogeme.expressions import Derive, Beta, log, exp, logzero
from biogeme.models import loglogit
from matplotlib import pyplot as plt

from optima_variables import (
    database,
    Choice,
    normalizedWeight,
    TimePT,
    TimeCar,
    MarginalCostPT,
    CostCarCHF,
    distance_km,
    NbTransf,
    fulltime,
    notfulltime,
    male,
    female,
    unreportedGender,
)


The objective of this laboratory is to calculate the willingness to pay for the improvement of some attributes.

Consider the two models introduced below. For each of them, perform the following calculations:

- Calculate the value of time for each individual in the sample for the public transportation alternative, and plot the distribution.
- Calculate the value of time for each individual in the sample for the car alternative, and plot the distribution.
- Calculate the average value in the population of these two quantities.
- Calculate the willingness to pay to save one transfer for each individual in the sample, and plot the distribution.

Hints:
- Take into account that the variable 'NbTransf' is discrete, and not continuous.
- The non linear model involves logarithms, that require a positive argument.

# First model

In the first model, the variables involved for the calculation of the willingness to pay appear linearly in the
utility functions.

Parameters to be estimated.

In [ ]:
ASC_CAR = Beta('asc_car', 0, None, None, 0)
ASC_SM = Beta('asc_sm', 0, None, None, 0)
BETA_TIME_FULLTIME_PT = Beta('BETA_TIME_FULLTIME_PT', 0, None, None, 0)
BETA_TIME_OTHER_PT = Beta('BETA_TIME_OTHER_PT', 0, None, None, 0)
BETA_TIME_FULLTIME_CAR = Beta('BETA_TIME_FULLTIME_CAR', 0, None, None, 0)
BETA_TIME_OTHER_CAR = Beta('BETA_TIME_OTHER_CAR', 0, None, None, 0)

BETA_DIST_MALE = Beta('BETA_DIST_MALE', 0, None, None, 0)
BETA_DIST_FEMALE = Beta('BETA_DIST_FEMALE', 0, None, None, 0)
BETA_DIST_UNREPORTED = Beta('BETA_DIST_UNREPORTED', 0, None, None, 0)
BETA_COST = Beta('BETA_COST', 0, None, None, 0)
BETA_TRANSF = Beta('BETA_TRANSF', 0, None, None, 0)


Utility functions

In [ ]:
V_PT = (
    BETA_TIME_FULLTIME_PT * TimePT * fulltime
    + BETA_TIME_OTHER_PT * TimePT * notfulltime
    + BETA_COST * MarginalCostPT
    + BETA_TRANSF * NbTransf
)
V_CAR = (
    ASC_CAR
    + BETA_TIME_FULLTIME_CAR * TimeCar * fulltime
    + BETA_TIME_OTHER_CAR * TimeCar * notfulltime
    + BETA_COST * CostCarCHF
)
V_SM = (
    ASC_SM
    + BETA_DIST_MALE * distance_km * male
    + BETA_DIST_FEMALE * distance_km * female
    + BETA_DIST_UNREPORTED * distance_km * unreportedGender
)
V = {0: V_PT, 1: V_CAR, 2: V_SM}


Estimation of the parameters

In [ ]:
logprob = loglogit(V, None, Choice)
biogeme = BIOGEME(database, logprob)
biogeme.modelName = 'wtp_first_model'
results = biogeme.estimate()


General statistics

In [ ]:
print(results.print_general_statistics())


Estimated parameters.

In [ ]:
parameters = results.get_estimated_parameters()
display(parameters)


# Second model: linear model in willingness to pay space.

Consider the moneymetric specification of the above model, and use it to calculate the same willingness to pay
indicators.

# Third model: non linear transformation of the variables

We use a Biogeme expression that returns the log of a variable if it is non zero, and 0 otherwise.
The variable is assumed to be non negative.

In [ ]:
V_PT = (
    BETA_TIME_FULLTIME_PT * logzero(TimePT) * fulltime
    + BETA_TIME_OTHER_PT * logzero(TimePT) * notfulltime
    + BETA_COST * logzero(MarginalCostPT)
    + BETA_TRANSF * logzero(NbTransf)
)
V_CAR = (
    ASC_CAR
    + BETA_TIME_FULLTIME_CAR * logzero(TimeCar) * fulltime
    + BETA_TIME_OTHER_CAR * logzero(TimeCar) * notfulltime
    + BETA_COST * logzero(CostCarCHF)
)
V_SM = (
    ASC_SM
    + BETA_DIST_MALE * distance_km * male
    + BETA_DIST_FEMALE * distance_km * female
    + BETA_DIST_UNREPORTED * distance_km * unreportedGender
)
V = {0: V_PT, 1: V_CAR, 2: V_SM}


Estimation of the parameters

In [ ]:
logprob = loglogit(V, None, Choice)
biogeme = BIOGEME(database, logprob)
biogeme.modelName = 'wtp_second_model'
results_third = biogeme.estimate()


General statistics

In [ ]:
print(results_third.print_general_statistics())


Estimated parameters

In [ ]:
parameters_third = results_third.get_estimated_parameters()
display(parameters_third)